In [169]:
import numpy as np
import pandas as pd
from sklearn.linear_model import Lasso,LassoCV,LassoLarsCV, RidgeCV, SGDRegressor
from sklearn.model_selection import train_test_split, KFold
from sklearn.metrics import mean_squared_error

## Data Loading

In [2]:
    # Data loading
    data = pd.read_csv("train.csv")
    y = data["y"].to_numpy()
    data = data.drop(columns=["Id", "y"])
    # print a few data samples
    print(data.head())

    X = data.to_numpy()

     x1    x2    x3    x4    x5
0  0.02  0.05 -0.09 -0.43 -0.08
1 -0.13  0.11 -0.08 -0.29 -0.03
2  0.08  0.06 -0.07 -0.41 -0.03
3  0.02 -0.12  0.01 -0.43 -0.02
4 -0.14 -0.12 -0.08 -0.02 -0.08


In [18]:
X[:,0].size

700

## function 

In [82]:
def calculate_RMSE(w, X, y):
    """This function takes test data points (X and y), and computes the empirical RMSE of 
    predicting y from X using a linear model with weights w. 

    Parameters
    ----------
    w: array of floats: dim = (13,), optimal parameters of ridge regression 
    X: matrix of floats, dim = (15,13), inputs with 13 features
    y: array of floats, dim = (15,), input labels

    Returns
    ----------
    RMSE: float: dim = 1, RMSE value
    """
    RMSE = 0
    # TODO: Enter your code here
#     y_pred = X @ w
#     RMSE = sqrt(np.sum(y - y_pred) ** 2)
    y_pred = np.matmul(X, w)
    RMSE = mean_squared_error(y, y_pred, squared=False)
    assert np.isscalar(RMSE)
    return RMSE

## Data transformation

### Test 

In [3]:
X_transformed = np.zeros((700, 21))

In [14]:
X_transformed[:,0].shape

(700,)

In [23]:
# Linear
X_transformed[:,0:5] = X

In [31]:
# Quadratic
X_transformed[:,5:10] = np.multiply(X, X)

In [29]:
# Exponential
X_transformed[:,10:15] = np.exp(X)

In [33]:
# Cosine
X_transformed[:,15:20] = np.cos(X)

In [34]:
# Constant
X_transformed[:,20] = 1

In [38]:
X[0,:]

array([ 0.02,  0.05, -0.09, -0.43, -0.08])

In [37]:
X_transformed[0,:]

array([ 2.00000000e-02,  5.00000000e-02, -9.00000000e-02, -4.30000000e-01,
       -8.00000000e-02,  4.00000000e-04,  2.50000000e-03,  8.10000000e-03,
        1.84900000e-01,  6.40000000e-03,  1.02020134e+00,  1.05127110e+00,
        9.13931185e-01,  6.50509095e-01,  9.23116346e-01,  9.99800007e-01,
        9.98750260e-01,  9.95952733e-01,  9.08965750e-01,  9.96801706e-01,
        1.00000000e+00])

### Function Implement

In [39]:
## function
def transform_data(X):
    """
    This function transforms the 5 input features of matrix X (x_i denoting the i-th component of X) 
    into 21 new features phi(X) in the following manner:
    5 linear features: phi_1(X) = x_1, phi_2(X) = x_2, phi_3(X) = x_3, phi_4(X) = x_4, phi_5(X) = x_5
    5 quadratic features: phi_6(X) = x_1^2, phi_7(X) = x_2^2, phi_8(X) = x_3^2, phi_9(X) = x_4^2, phi_10(X) = x_5^2
    5 exponential features: phi_11(X) = exp(x_1), phi_12(X) = exp(x_2), phi_13(X) = exp(x_3), phi_14(X) = exp(x_4), phi_15(X) = exp(x_5)
    5 cosine features: phi_16(X) = cos(x_1), phi_17(X) = cos(x_2), phi_18(X) = cos(x_3), phi_19(X) = cos(x_4), phi_20(X) = cos(x_5)
    1 constant features: phi_21(X)=1

    Parameters
    ----------
    X: matrix of floats, dim = (700,5), inputs with 5 features

    Returns
    ----------
    X_transformed: array of floats: dim = (700,21), transformed input with 21 features
    """
    X_transformed = np.zeros((700, 21))
    # TODO: Enter your code here
    # Linear
    X_transformed[:,0:5] = X
    # Quadratic
    X_transformed[:,5:10] = np.multiply(X, X)
    # Exponential
    X_transformed[:,10:15] = np.exp(X)
    # Cosine
    X_transformed[:,15:20] = np.cos(X)
    # Constant
    X_transformed[:,20] = 1
    assert X_transformed.shape == (700, 21)
    return X_transformed



##  Fit

### Test

In [67]:
weight = np.zeros((21,))

In [43]:
# 划分测试集和训练集
xtrain,xtest,ytrain,ytest = train_test_split(X_transformed, y, test_size=0.3)

In [148]:
# 自己建立Lasso进行alpha选择的范围
# 形成10为底的指数函数
# 10**（-10） -10**（-2）
alpha_range = np.logspace(-10, 2, 5000, base=10)
# print(alpha_range) # 200个自定义的alpha值

In [94]:
alpha_range

array([1.00000000e-10, 1.00693306e-10, 1.01391419e-10, ...,
       9.86276760e+04, 9.93114676e+04, 1.00000000e+05])

### Lasso 

In [141]:
Lasso?

In [142]:
lasso = Lasso(max_iter = 10000, alpha = 0.003, random_state = 99).fit(xtrain,ytrain)

In [143]:
calculate_RMSE(lasso.coef_, xtest, ytest)

6.712226277078754

### LassoCV

In [149]:
lasso_ = LassoCV(alphas=alpha_range,random_state = 99, cv=5).fit(xtrain,ytrain)

/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 0.1876256292925973, tolerance: 0.1455072851934822
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 0.3262214198523452, tolerance: 0.1455072851934822
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 0.5823348364037884, tolerance: 0.1455072851934822
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAI

/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 138.7214017600685, tolerance: 0.1455072851934822
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 138.81223347326943, tolerance: 0.1455072851934822
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 138.89991623187132, tolerance: 0.1455072851934822
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIM

/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 534.7737703287768, tolerance: 0.1455072851934822
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 535.3674746644599, tolerance: 0.1455072851934822
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 535.9584862234667, tolerance: 0.1455072851934822
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/

/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 654.0550996491731, tolerance: 0.1455072851934822
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 654.2207749143403, tolerance: 0.1455072851934822
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 654.3858311563943, tolerance: 0.1455072851934822
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/

/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 683.9140850209936, tolerance: 0.1455072851934822
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 683.9602516731331, tolerance: 0.1455072851934822
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 684.0062451739612, tolerance: 0.1455072851934822
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/

...

/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 669.9724995428268, tolerance: 0.15265454914286708
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 670.2737636437032, tolerance: 0.15265454914286708
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 670.5729213809356, tolerance: 0.15265454914286708
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAI

/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 710.6881810762571, tolerance: 0.15265454914286708
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 710.7354333756405, tolerance: 0.15265454914286708
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 710.7824269194708, tolerance: 0.15265454914286708
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAI

/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 717.7827275407884, tolerance: 0.15265454914286708
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 717.7914570842185, tolerance: 0.15265454914286708
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 717.8001382466659, tolerance: 0.15265454914286708
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAI

/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 719.0402852513597, tolerance: 0.15265454914286708
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 719.0415572201009, tolerance: 0.15265454914286708
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 719.0428197396358, tolerance: 0.15265454914286708
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAI

/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 719.1580329860341, tolerance: 0.15265454914286708
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 719.1579104514425, tolerance: 0.15265454914286708
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 719.157786394325, tolerance: 0.15265454914286708
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIM

In [150]:
lasso_2 = LassoCV(alphas=alpha_range,random_state = 99, cv=5).fit(X_transformed, y)

/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 0.23603424824250396, tolerance: 0.22163627805456168
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 0.6423233080167847, tolerance: 0.22163627805456168
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 1.4116422655656606, tolerance: 0.22163627805456168
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs

/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 29.66561946609363, tolerance: 0.22163627805456168
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 29.638768509211104, tolerance: 0.22163627805456168
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 29.613841896013582, tolerance: 0.22163627805456168
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/P

/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 270.6145802721485, tolerance: 0.22163627805456168
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 275.6293663134081, tolerance: 0.22163627805456168
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 281.12281376282976, tolerance: 0.22163627805456168
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PA

/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 600.5670718524766, tolerance: 0.22163627805456168
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 602.1473704444048, tolerance: 0.22163627805456168
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 603.7113673900107, tolerance: 0.22163627805456168
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAI

/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 773.2865253812869, tolerance: 0.22163627805456168
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 773.5130739008155, tolerance: 0.22163627805456168
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 773.7364432598806, tolerance: 0.22163627805456168
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAI

...

/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 728.3203453877021, tolerance: 0.2133363662509789
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 728.5878880758946, tolerance: 0.2133363662509789
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 728.8549301075886, tolerance: 0.2133363662509789
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/

/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 918.3738911198295, tolerance: 0.2133363662509789
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 918.8606907511929, tolerance: 0.2133363662509789
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 919.3450653052723, tolerance: 0.2133363662509789
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/

/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 996.2678413287931, tolerance: 0.2133363662509789
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 996.3793358336452, tolerance: 0.2133363662509789
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 996.4902184159384, tolerance: 0.2133363662509789
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/

/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 1013.430690871371, tolerance: 0.2133363662509789
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 1013.453529648762, tolerance: 0.2133363662509789
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 1013.4762575639137, tolerance: 0.2133363662509789
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML

/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 1017.1177806787174, tolerance: 0.2133363662509789
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 1017.1228437067883, tolerance: 0.2133363662509789
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIML/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 1017.127882285297, tolerance: 0.2133363662509789
  model = cd_fast.enet_coordinate_descent_gram(
/home/mullin/anaconda3/envs/PAIM

In [97]:
# 查看最佳正则化系数
best_alpha = lasso_2.alpha_ 

In [57]:
best_alpha

0.005231099308056258

In [151]:
calculate_RMSE(lasso_2.coef_, xtest, ytest)

6.8397530029631275

In [152]:
calculate_RMSE(lasso_.coef_, xtest, ytest)

6.726225819155936

### Linear

In [161]:
Linear_ = LinearRegression(fit_intercept=False)

In [162]:
Linear_.fit(xtrain,ytrain)

LinearRegression(fit_intercept=False)

In [163]:
calculate_RMSE(Linear_.coef_, xtest, ytest)

2.009794429103758

In [164]:
LinearRegression?

### Ridge 

In [153]:
ridge_ = RidgeCV(alphas=alpha_range,cv=5).fit(xtrain,ytrain)

In [154]:
ridge_2 = RidgeCV(alphas=alpha_range,cv=5).fit(X_transformed, y)

In [155]:
ridge_.alpha_

3.0067382268278893

In [156]:
ridge_.coef_

array([-0.17442977, -0.66320833, -1.08256904, -0.1091135 ,  0.25080564,
       -0.09026412,  0.12925132,  0.17498222, -0.08812798,  0.16786898,
       -0.2252949 , -0.58979168, -1.0029686 , -0.15604641,  0.31642832,
        0.04539848, -0.06501643, -0.08709717,  0.04172114, -0.08077001,
        0.        ])

In [157]:
calculate_RMSE(ridge_.coef_, xtest, ytest)

5.187054324153009

In [158]:
ridge_2.alpha_

4.143081386977407

In [159]:
ridge_2.coef_

array([-0.04561099, -0.73067749, -0.90817081, -0.05006783, -0.05286317,
       -0.30418063,  0.23150991,  0.18600949, -0.0489827 ,  0.13780532,
       -0.20824902, -0.61881308, -0.82439738, -0.08497207,  0.00322509,
        0.15117053, -0.11513079, -0.0923644 ,  0.02329639, -0.06676337,
        0.        ])

In [160]:
calculate_RMSE(ridge_2.coef_, xtest, ytest)

5.1320290817119805

### SGDRegressor 

In [186]:
SGDRegressor?

In [196]:
SGD = SGDRegressor(loss='squared_error', penalty='l2', fit_intercept=False, random_state=0)

In [197]:
SGD.fit(X_transformed, y)

SGDRegressor(fit_intercept=False, loss='epsilon_insensitive', random_state=0)

In [198]:
calculate_RMSE(SGD.coef_, xtest, ytest)

1.953710203763454

### SGDRegressor CV

In [254]:
loss_range = ['squared_error',  'epsilon_insensitive',  'squared_epsilon_insensitive', 'huber']
penalty_range = ['l1',  'l2']
n_folds = 10

In [212]:
loss_range[1]

'huber'

In [213]:
for loss in loss_range:
    for penalty in penalty_range:
        SGD = SGDRegressor(loss=loss, penalty=penalty, fit_intercept=False, random_state=0).fit(xtrain, ytrain)
        print(loss)
        print(penalty)
        print(calculate_RMSE(SGD.coef_, xtest, ytest))

squared_error
l1
1.9621953465899433
squared_error
l2
1.9621841024289959
huber
l1
1.9556076801949525
huber
l2
1.955557452525074
epsilon_insensitive
l1
1.9533963278014046
epsilon_insensitive
l2
1.953265847356308
squared_epsilon_insensitive
l1
1.9500313591820229
squared_epsilon_insensitive
l2
1.9500119619069864


In [225]:
def fit_SGD(X, y, loss, penalty):

    w = np.zeros((13,))
    # TODO: Enter your code here
    SGD = SGDRegressor(loss=loss, penalty=penalty, fit_intercept=False, random_state=0).fit(xtrain, ytrain)
    w = SGD.coef_
    assert w.shape == (21,)
    return w

In [271]:
def select_model(X, y, loss_range, penalty_range, n_folds):
    RMSE_mat = np.zeros((n_folds, len(loss_range), len(penalty_range)))
    kf = KFold(n_splits = n_folds)
    for index_loss, loss in enumerate(loss_range):
        for index_pen,penalty in enumerate(penalty_range):
            index_kSet = 0
            for train_index, valid_index in kf.split(X):
                weight = fit_SGD(X[train_index], y[train_index], loss, penalty)
                RMSE = calculate_RMSE(weight, X[valid_index], y[valid_index])
                RMSE_mat[index_kSet, index_loss, index_pen] = RMSE
                index_kSet= index_kSet + 1
                        
    avg_RMSE = np.mean(RMSE_mat, axis=0)
    best_para = [loss_range[np.argmin([avg_RMSE])%3], penalty_range[np.argmin([avg_RMSE])%2]]
    return avg_RMSE, best_para

In [272]:
avg_RMSE,best_para = select_model(X_transformed, y, loss_range, penalty_range, n_folds)

In [273]:
avg_RMSE

array([[1.95093182, 1.95091754],
       [1.94625691, 1.94620246],
       [1.94137337, 1.94135809],
       [1.9480648 , 1.94804093]])

In [275]:
best_para

['squared_epsilon_insensitive', 'l2']

In [277]:
w_SGD = SGDRegressor(loss = best_para[0], penalty = best_para[1], fit_intercept=False, random_state=0).fit(X_transformed, y)

In [280]:
w_SGD

SGDRegressor(fit_intercept=False, loss='squared_epsilon_insensitive',
             random_state=0)

### Function Implement 

In [278]:
w = w_SGD

In [279]:
np.savetxt("./results.csv", w, fmt="%.12f")

ValueError: Expected 1D or 2D array, got 0D array instead

In [128]:
w

array([ 2.79467625, -2.36449489, -1.35632948,  2.58610323, -0.18090526,
       -2.43574137,  2.60705309,  2.80781925,  0.66788948,  6.38342632,
       -3.14749629,  0.8568762 , -0.91511832, -2.69805024,  1.91531242,
        1.3870039 , -1.42218547, -1.31021913, -0.49885508, -2.9299436 ,
        0.        ])

[ 6.62159306 -5.21058439 -1.36003242  7.06248808 -0.52948709 -0.2185518
  2.13810967  3.76680927  2.71728928  7.5252329  -6.94040494  3.68717124
 -0.87612654 -7.12829856  2.42435479  2.32225476  0.15700074  0.05849815
 -0.40078346 -1.42872466  1.6447392 ]

In [165]:
w_r = np.array([ 6.62159306, -5.21058439, -1.36003242,  7.06248808, -0.52948709, -0.2185518,
  2.13810967,  3.76680927,  2.71728928,  7.5252329,  -6.94040494,  3.68717124,
 -0.87612654, -7.12829856,  2.42435479,  2.32225476,  0.15700074,  0.05849815,
 -0.40078346, -1.42872466,  1.6447392])

In [167]:
calculate_RMSE(w_r, xtest, ytest)

1.9376074287707847